In [135]:
import os 
import numpy as np
import random
import math
from sklearn.metrics import average_precision_score
import pandas as pd

In [136]:
#從grid_search_weight中找尋不同的file 
path = '../Data/grid_search_weight/0113/'
files = os.listdir(path)
len(files)
np.load(path+files[0])['U'].shape

(200, 128)

In [137]:
def square_sum(pars):
    all_squ_sum = []
    for par in pars:
        all_squ_sum.append(np.sum(np.multiply(par,par)))
    return all_squ_sum 
def shape_sum(pars):
    all_shape = []
    for par in pars:
        all_shape.append(par.shape)
    return all_shape
def relu(x):
    return np.maximum(0,x)  

def softmax(x):
    exp_x = np.exp(x)
    softmax_x = exp_x / np.sum(exp_x)
    return softmax_x 

def sigmoid(z):
    return 1 / (1 + np.exp(-z))  

In [148]:
user_following = np.load('../Data/npy/user_following_1489.npy')[:100]
all_3374 = np.load('../Data/npy/all_3374D.npy')
user_category = np.load('../Data/npy/user_category_1489.npy')[:100]
YouTuber_category = np.load('../Data/npy/YouTuber_category_0.7.npy')
active_users = np.load('../Data/npy/active_userID_1489.npy')[:100]
#The number of followers for each YouTuber
YouTuber_followers = np.sum(user_following, axis=0)
print(YouTuber_followers)
over5 = 0
for num in YouTuber_followers:
    if num >= 5:
        over5+=1
print('The num of followers over 5:',over5)
user_category_norm = np.zeros(user_category.shape)
for i in range(len(user_category)):
    user_category_norm[i] = user_category[i]/np.max(user_category[i])
print('user_category after normalized by max...')
print('user_category_norm shape ',user_category_norm.shape)
following_true = [0]*len(user_following)
for i in range(len(user_following)):
    each_user = []
    for j in range(len(user_following[i])):
        if user_following[i][j] == 1:
            each_user.append(j)
    following_true[i] = each_user
#print(following_true)
#最少跟最多的following 
minlen = 10000
maxlen = 0
num_of_follower = []
for i in range(len(following_true)):
    if len(following_true[i]) < minlen:
        minlen = len(following_true[i])
    if len(following_true[i]) > maxlen:
        maxlen = len(following_true[i])
    num_of_follower.append(len(following_true[i]))
print('Min number of followings ',minlen)
print('Max number of followings ',maxlen)
test_amount = 10
yt_test_amount = 18
user_idx = [i for i in range(len(user_following))]
#user_idx = user_idx_over10
#test_idx is the number of user for testing
random.seed(5)
test_idx = random.sample(user_idx,test_amount)
# Training  and Testing --New
train_t = [0]*(len(user_following))
train_f = [0]*(len(user_following))
# Testing 
test_t = [0]*test_amount
test_f = [0]*test_amount
test_pos = -1

for i in range(len(user_following)):
    t_for_train = []
    f_for_train = []
    if i not in test_idx: #if not in test id, just append it to true or false list
        for j in range(88):
            if user_following[i][j] == 1:
                t_for_train.append(j)
            else:
                f_for_train.append(j)
        train_t[i] = t_for_train
        train_f[i] = f_for_train
        
    else: #if in test id, choose 2 true and other 
        test_pos += 1
        temp_t = []
        temp_f = []
        for j in range(88):
            if user_following[i][j] == 1:
                temp_t.append(j)
            else:
                temp_f.append(j)
        #print(len(temp_t),math.ceil(0.5*len(temp_t)))
        t_for_test = random.sample(temp_t,math.ceil(0.5*len(temp_t)))
        f_for_test  = random.sample(temp_f,yt_test_amount-len(t_for_test))
        
        test_t[test_pos] = t_for_test
        test_f[test_pos] = f_for_test
        
        #other for training
        t_for_train = [item for item in temp_t if not item in t_for_test]
        #print(len(t_for_train ))
        f_for_train = [item for item in temp_f if not item in f_for_test]
        train_t[i] = t_for_train
        train_f[i] = f_for_train
total_test = 0
for t in test_t:
    total_test += len(t)
avg = total_test/test_amount
print(avg)

[ 8  0  2 24  1  0  0 11 47  7 25 32 10  1 16  1  6 24  3  2  1  6  4  0
 39 39 10 16 27 22  0  2 17 15  0  2  0  8  2  1 28 16  3 33  9 24  0  3
  0  9  0  0  0  2 28  2  2 18  0  3 23  0  2 39  0  1  1 65  0  2 18 21
  7  1 47 14 19  1  3 66  3  0 28  3 20  0  6  0]
The num of followers over 5: 42
user_category after normalized by max...
user_category_norm shape  (100, 17)
Min number of followings  5
Max number of followings  21
5.2


In [149]:
def getScoreMatrix(RS):
    #取出test的資料
    testRS = np.zeros((test_amount,yt_test_amount)) #shape 150*20
    target = np.zeros((test_amount,yt_test_amount))
    #test_t 是true的
    #test_f 是false的

    for z in range(test_amount):
        user_id = test_idx[z]
        #positive target YouTuber list
        youtube_t = test_t[z] 
        #not target YouTuber list
        youtube_f = test_f[z]

        #前兩個放target的RS
        for i in range(len(youtube_t)):
            testRS[z][i] = RS[z][youtube_t[i]]
            target[z][i] = 1
        for i in range(len(youtube_f)):
            testRS[z][i+len(youtube_t)] = RS[z][youtube_f[i]]
    sumtarget = 0
    for i in range(len(target)):
        #print(np.sum(target[i]))
        sumtarget += np.sum(target[i])
    print('num of positive data in testing:',sumtarget)
    print('total testing data:',test_amount*yt_test_amount)
    return target, testRS,sumtarget

def topN(sortlist,n):
    topList = []
    for i in range(n):
        topList.append(sortlist.index(max(sortlist)))
        #print(max(sortlist))
        #print(sortlist.index(max(sortlist)))
        sortlist[sortlist.index(max(sortlist))] = -1000000000
    return topList

def F1_score(prec,rec):
    f1 = (2*prec*rec)/(prec+rec)
    return f1

In [150]:
def getTOP1(target,testRS,sumtarget):
    print('top1')
    correct = 0
    for i in range(len(testRS)):
        top_0 = topN(list(testRS[i]),1) #取一個
        
        #print(top_0)
        if top_0[0] < int(np.sum(target[i])):
            correct += 1
    top1_prec = correct/len(testRS)
    top1_recall = correct/(sumtarget)
    print('prec ',top1_prec,'recall ',top1_recall)
    #f1 score
    print('F1_score:',F1_score(top1_prec,top1_recall))
def getTOP3(target,testRS,sumtarget):
    print('top3')
    correct = 0
    for i in range(len(testRS)):
        top_3 = topN(list(testRS[i]),3) #取一個
        
        #print(top_3)
        for j in range(len(top_3)):
            if top_3[j] < int(np.sum(target[i])):
                correct += 1
    top3_prec = correct/(len(testRS)*3)
    top3_recall = correct/(sumtarget)
    print('prec ',top3_prec,'recall ',top3_recall)
    #f1 score
    print('F1_score:',F1_score(top3_prec,top3_recall))
    
def getTOP5(target,testRS,sumtarget):
    print('top5')
    correct = 0
    for i in range(len(testRS)):
        top_5 = topN(list(testRS[i]),5) #取一個
       
        #print(top_5)
        for j in range(len(top_5)):
            if top_5[j] < int(np.sum(target[i])):
                correct += 1
    top5_prec = correct/(len(testRS)*5)
    top5_recall = correct/(sumtarget)
    print('prec ',top5_prec,'recall ',top5_recall)
    #f1 score
    print('F1_score:',F1_score(top5_prec,top5_recall))

In [153]:
"""
NDCG
https://daiwk.github.io/posts/nlp-ndcg.html
"""
# pre_list
"""
test_amount = 150
yt_test_amount = 20
"""
def NDCG(target,testRS):
    all_sort = []
    num_ndcg = 10
    pre_matrix = np.zeros(shape=(test_amount,yt_test_amount))
    for i in range(test_amount):
        top_n = topN(list(testRS[i]),num_ndcg) #取一個
        #print(top_n)
        all_sort.append(topN(list(testRS[i]),len(testRS[i])))
        for j in range(len(top_n)):
            pre_matrix[i][top_n[j]] = 1

    #Ideal DCG，理想状况下的DCG。也就是说，相关性完全由高到低排序时算出的DCG：
    def IDCG(ideal_list): #ideal_list example = [1,1,1,1,1,0,0,....]
        idcg=0
        #print('ideal',ideal_list)
        for i in range(len(ideal_list)):
            #print((2**true_list[i]-1),math.log2(i+2))
            idcg+= (2**ideal_list[i]-1)/ math.log2(i+2)
        #print('idcg',idcg)
        return idcg
    def DCG(prec_list): #找出前n名的[1,1,1,0,...]
        dcg=0
        print('prec',prec_list)
        for i in range(len(prec_list)):
            dcg+= (2**prec_list[i]-1)/ math.log2(i+2)
        #print('dcg',dcg)
        return dcg
    total_ndcg = 0
    
    for m in range(test_amount): # the number of testing users
        idcg = IDCG(target[m][:num_ndcg])
        pre_list = []
        for s in all_sort[m][:num_ndcg]:
            #print(s)
            #print(target[m][s])
            pre_list.append(target[m][s]) #把prec_list 的 score加進去
        dcg = DCG(pre_list)
        ndcg = dcg/idcg
        #print(ndcg)
        total_ndcg += ndcg
    avg_ndcg = total_ndcg/test_amount
    print('NDCG:',avg_ndcg)
    return pre_matrix,avg_ndcg

# MAP
"""
>>> y_true = np.array([0, 0, 1, 1])
>>> y_scores = np.array([0.1, 0.4, 0.35, 0.8])
>>> average_precision_score(y_true, y_scores)
"""
def MAP(target,pre_matrix):
    total_prec = 0
    for u in range(test_amount):
        y_true = target[u]
        y_scores = pre_matrix[u]
        total_prec+=average_precision_score(y_true, y_scores)
    Map_value = total_prec/test_amount
    print('MAP',Map_value)
    return Map_value

In [156]:
def testing(U, Y, A, E,Au, Ay, Aa, Av,B):
    print(U.shape)
    print(Y.shape)
    print(A.shape)
    print(np.max(Au))
    print(np.max(Ay))
    print(np.max(Aa))
    print(np.max(Av))
    print(np.max(B))
    result=np.zeros((test_amount,88))
    RS=np.zeros((test_amount,88))
    #test_idx --> Test 的 index
    sum_alpha = 0
    for s in range(test_amount):
        print(s,test_idx[s])

        yes=[]
        #sample=random.sample(train_t[test_idx[s]],len(train_t[test_idx[s]])) #從training part 的positive feedback 取出YouTuber 當成Auxilary
        sample = train_t[test_idx[s]]
        #sample=result_yes_id[now]
        alpha=np.zeros([len(sample)])

        for a in range(len(sample)):
            r =np.max(YouTuber_category[sample[a]]*user_category_norm[test_idx[s]]) #sample a 的category vec *user_category vec
            
            alpha_a = np.dot(Au[test_idx[s]][sample[a]],np.expand_dims(U[test_idx[s]],0).T)+np.dot(Ay[test_idx[s]][sample[a]],np.expand_dims(Y[sample[a]],0).T)+np.dot(Aa[test_idx[s]][sample[a]],
                    np.expand_dims(A[sample[a]],0).T)+ np.dot(Av[test_idx[s]][sample[a]],np.expand_dims(all_3374[sample[a]],0).T)
            """
            relu part ...
            """
            alpha[a]=np.sum((relu(alpha_a)))*r
            """
            tanh part ...
            """
            #alpha[a]=np.sum((np.tanh(alpha_a)))*r
            
            
        mul=np.zeros((1,128))
        #print('alpha--------',alpha)
        #print('add alpha------------',np.add(alpha,0.000000001))
        added_alpha = np.add(alpha,0.000000001)
        norm_alpha = added_alpha/np.sum(added_alpha)
        print('alpha-----------',alpha)
        print('norm alpha--------------',norm_alpha)
        sum_alpha += np.sum(alpha)
        for i in range(len(sample)):
            mul+=norm_alpha[i]*A[sample[i]] #attention alpha*Ai part
        new_mul=mul+U[test_idx[s]]  #(U+auxilary)
    
        
        
        for k in range(88):
            result[s][k]=np.dot(new_mul,Y[k].T) #(U+auxilary)*photo latent factor
            RS[s][k] = np.dot(new_mul,Y[k].T)+np.dot(B[test_idx[s]],np.dot(E, all_3374[k].T))
            
            print('================================')
            print('U',np.sum(U[test_idx[s]] ))
            print('A',np.sum(mul))
            print('Y',np.sum(Y[k]))
            print('B',np.sum(B[test_idx[s]]))
            print('E',np.sum(np.dot(E, all_3374[k].T)))
            
            print('Former',np.dot(new_mul,Y[k].T))
            print('Later',np.dot(B[test_idx[s]],np.dot(E, all_3374[k].T)))
            print('RS',np.dot(new_mul,Y[k].T)+np.dot(B[test_idx[s]],np.dot(E, all_3374[k].T)))
            print('--------------------------------')
            
    print('sum_alpha',sum_alpha)
    return RS

In [157]:
import os 
#從grid_search_weight中找尋不同的file 
path = '../Data/grid_search_weight/0110_88all_Relu/'
all_files = os.listdir(path)
#print(files)
par_files = list(set([file.split('_Edims')[0] for file in all_files]))
print(par_files)
for par_file in par_files:
    NDCG_List = []
    MAP_List = []
    DIM_List = []
    csv_path = '../Data/grid_search_weight/CSV_Tan/'
    for file in all_files:
        if par_file in file:
            print(par_file,file)
            par_data = np.load(path+file)
            U = par_data['U']
            Y = par_data['Y']
            A = par_data['A']
            E = par_data['E']
            #W1 = par_data['W1']
            Wu = par_data['Wu']
            Wy = par_data['Wy']
            Wa = par_data['Wa']
            Wv = par_data['Wv']
            B = par_data['B']
            RS = testing(U, Y, A, E,Wu, Wy, Wa, Wv,B)
            target,testRS,sumtarget = getScoreMatrix(RS)
            getTOP1(target,testRS,sumtarget)
            getTOP3(target,testRS,sumtarget)
            getTOP5(target,testRS,sumtarget)
            pre_matrix,avg_ndcg = NDCG(target,testRS)
            Map_value = MAP(target,pre_matrix)
            NDCG_List.append(avg_ndcg)
            MAP_List.append(Map_value)
            DIM_List.append(file.split('Edims')[1].split('.npz')[0])
            print('--------------------------------------------------------------------------------------------')
    #print(NDCG_List)
    #print(DIM_List)
    result_dict = {'Dims':DIM_List,'NDCG':NDCG_List,'MAP':MAP_List}
    df = pd.DataFrame(result_dict)
    #df.to_csv(csv_path+par_file+'.csv',index=False)

['0.01_0.01_1_0.01', '0.01_0.1_1_0.01', '0.001_0.001_0.01_0.01', '0.01_0.1_0.01_0.1', '0.01_0.1_0.1_1', '0.01_0.01_1_0.1', '0.01_0.1_0.1_0.01', '0.01_0.01_0.1_0.01', '0.01_0.01_0.01_0.01', '0.01_0.01_0.1_1', '0.01_0.01_1_1', '0.01_0.1_0.01_1', '0.01_0.1_1_0.1', '0.01_0.01_0.01_1', '0.01_0.01_0.01_0.1', '0.01_0.1_0.01_0.01', '0.01_0.01_0.1_0.1', '0.01_0.1_0.1_0.1']
0.01_0.01_1_0.01 0.01_0.01_1_0.01_Edims50.npz
(100, 128)
(88, 128)
(88, 128)
6.991016e-05
7.000797e-05
7.0803304e-05
7.764616e-05
0.10879946
0 79
alpha----------- [0.00000000e+00 1.59926330e-05 0.00000000e+00 1.77617676e-04
 4.31858677e-05]
norm alpha-------------- [4.22295198e-06 6.75403443e-02 4.22295198e-06 7.50075141e-01
 1.82376068e-01]
U 0.042929932
A -0.12184514189372986
Y -0.06446099
B 1.2387515
E 9.771793564500436
Former [0.05795764]
Later -0.7171442871167762
RS [-0.65918664]
--------------------------------
U 0.042929932
A -0.12184514189372986
Y 2.3804219
B 1.2387515
E 37.272198985747956
Former [0.01254485]
Later 0.

RS [0.74871011]
--------------------------------
U 0.042929932
A -0.12184514189372986
Y -0.31727773
B 1.2387515
E -1.1898985968670865
Former [-0.02107796]
Later -1.1548332279752762
RS [-1.17591119]
--------------------------------
U 0.042929932
A -0.12184514189372986
Y 2.2370908
B 1.2387515
E 37.920534370104974
Former [-0.0310285]
Later 0.8482454882682199
RS [0.81721699]
--------------------------------
U 0.042929932
A -0.12184514189372986
Y 1.0500687
B 1.2387515
E 3.016896726212212
Former [0.11379699]
Later -1.2684877096690899
RS [-1.15469072]
--------------------------------
U 0.042929932
A -0.12184514189372986
Y -1.6024646
B 1.2387515
E 114.51478049417958
Former [-0.03342524]
Later 3.42552012409597
RS [3.39209488]
--------------------------------
U 0.042929932
A -0.12184514189372986
Y 1.6895895
B 1.2387515
E 9.053612848579025
Former [0.00882848]
Later -0.8356977046349149
RS [-0.82686922]
--------------------------------
U 0.042929932
A -0.12184514189372986
Y 2.6296246
B 1.2387515
E 

Later 2.777612726317083
RS [2.84840805]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 2.559424
B 1.0484073
E 10.657199833206304
Former [0.16715771]
Later -0.7928786892611044
RS [-0.62572098]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 3.8649635
B 1.0484073
E 47.43167175679451
Former [-0.36483461]
Later 0.45881023453446934
RS [0.09397562]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 1.2163035
B 1.0484073
E 104.92010979269689
Former [-0.05385963]
Later 3.173047635280191
RS [3.11918801]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 1.6172287
B 1.0484073
E 51.52209069556001
Former [-0.43901974]
Later 1.2418010847159717
RS [0.80278135]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 1.3912933
B 1.0484073
E 50.5098686026129
Former [-0.09845264]
Later 0.5620359456993301
RS [0.46358331]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y -3.9749832
B 

RS [1.58709508]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 3.1421604
B 1.0484073
E 0.07978404288724583
Former [-0.22675068]
Later -0.7689893841354479
RS [-0.99574006]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 1.9867467
B 1.0484073
E 42.38839540999309
Former [-0.42073376]
Later -0.6907087736770745
RS [-1.11144253]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y -4.990709
B 1.0484073
E 70.52174374509177
Former [0.60750211]
Later 2.4210680250971794
RS [3.02857013]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 2.4443114
B 1.0484073
E 33.63987740184931
Former [-0.4739434]
Later 0.6560829908408619
RS [0.18213959]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 2.4755428
B 1.0484073
E 7.059377169770304
Former [-0.29879863]
Later -0.39011144554568317
RS [-0.68891008]
--------------------------------
U -0.003161204
A 0.6561231754301557
Y 4.1717806
B 1.0484073
E 104.534

RS [-0.00803534]
--------------------------------
U -0.05149556
A -0.41750076808535763
Y -0.19628185
B 0.80846703
E 44.09026021851324
Former [-0.15500158]
Later 0.8717710229511388
RS [0.71676945]
--------------------------------
U -0.05149556
A -0.41750076808535763
Y 4.657336
B 0.80846703
E 19.386446505766287
Former [-0.46294924]
Later 0.6094520663406731
RS [0.14650283]
--------------------------------
U -0.05149556
A -0.41750076808535763
Y -2.6758046
B 0.80846703
E 66.53667333390213
Former [0.14518627]
Later 3.201556082210012
RS [3.34674235]
--------------------------------
U -0.05149556
A -0.41750076808535763
Y -2.2541583
B 0.80846703
E 96.2487787116852
Former [0.47243198]
Later 1.4604206009031533
RS [1.93285258]
--------------------------------
U -0.05149556
A -0.41750076808535763
Y 1.7647082
B 0.80846703
E -3.4463017452219207
Former [0.04334911]
Later -1.0935134420057528
RS [-1.05016433]
--------------------------------
U -0.05149556
A -0.41750076808535763
Y 2.656777
B 0.80846703
E

...

E 23.60418185433138
Former [-0.428475]
Later 1.7682490264644068
RS [1.33977403]
--------------------------------
U -0.033410203
A -1.2331191898992984
Y 1.9992954
B 3.6664693
E 11.266253165899997
Former [-0.26175123]
Later 0.7930706665053932
RS [0.53131943]
--------------------------------
U -0.033410203
A -1.2331191898992984
Y 4.443962
B 3.6664693
E 41.87732081039089
Former [-0.4712205]
Later 3.1283903401406676
RS [2.65716984]
--------------------------------
U -0.033410203
A -1.2331191898992984
Y -4.833321
B 3.6664693
E 48.999498833488516
Former [0.73442926]
Later 3.690793090014128
RS [4.42522235]
--------------------------------
U -0.033410203
A -1.2331191898992984
Y 1.8712002
B 3.6664693
E 30.902022221917772
Former [-0.40640041]
Later 2.2171201131480647
RS [1.81071971]
--------------------------------
U -0.033410203
A -1.2331191898992984
Y 2.3526204
B 3.6664693
E 29.527322960940655
Former [-0.34669124]
Later 2.144063692281048
RS [1.79737245]
--------------------------------
U -0.033

E 15.169563505969426
Former [-0.49369955]
Later 0.7451544642118075
RS [0.25145492]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y -2.1342695
B 2.575715
E 41.75275636667776
Former [0.05856376]
Later 2.0836465253189456
RS [2.14221029]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y -2.1173592
B 2.575715
E 50.23436084291217
Former [0.77938217]
Later 2.5590066614379037
RS [3.33838883]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y 2.1976151
B 2.575715
E 42.45168344506216
Former [-0.32415957]
Later 2.319832911714804
RS [1.99567335]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y 2.332161
B 2.575715
E 39.83768278434027
Former [-0.04267828]
Later 2.084062258350865
RS [2.04138398]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y -2.414466
B 2.575715
E 29.09690118238168
Former [-0.21256368]
Later 1.451759263394381
RS [1.23919558]
--------------------------------
U -0.051975705
A 0

Later 2.7182138948347028
RS [3.41926849]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y -0.4529463
B 2.575715
E 31.61929917837308
Former [-0.07515695]
Later 1.7453895533670198
RS [1.6702326]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y 0.5362793
B 2.575715
E 28.071256100897003
Former [-0.60323997]
Later 1.4719656350036956
RS [0.86872566]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y -3.3205144
B 2.575715
E 45.77222500847907
Former [0.75013901]
Later 2.321276614382441
RS [3.07141563]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y 0.897244
B 2.575715
E 32.929145061004924
Former [-0.01950315]
Later 1.6379358188926532
RS [1.61843267]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y -4.651764
B 2.575715
E 27.888413053229424
Former [0.70082811]
Later 1.4121776609925896
RS [2.11300577]
--------------------------------
U -0.051975705
A 0.0681197366975661
Y 2.123289
B 2.57571

Later 0.7686251163294011
RS [0.42969739]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 2.3479562
B 1.9206525
E 48.69151468351838
Former [-0.41883886]
Later 0.2852298500105793
RS [-0.13360901]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 3.088504
B 1.9206525
E 20.31550440846612
Former [-0.16868115]
Later 0.632014168868143
RS [0.46333302]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 3.676689
B 1.9206525
E 50.885013133904536
Former [-0.04821304]
Later 0.883039078584015
RS [0.83482604]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 3.2265203
B 1.9206525
E 37.52391544313412
Former [-0.28706301]
Later 1.191408564442063
RS [0.90434555]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 0.5266725
B 1.9206525
E 33.97557052092593
Former [-0.02839697]
Later 1.0085665539681172
RS [0.98016959]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 3.7835238
B 1.92

RS [0.72771709]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y -0.18517792
B 1.9206525
E 53.519773487834115
Former [-0.52371816]
Later 2.3876957156227916
RS [1.86397756]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 3.1770887
B 1.9206525
E 27.72342005457752
Former [-0.20983037]
Later 0.17044353099660162
RS [-0.03938683]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 0.82188535
B 1.9206525
E 41.70361373482365
Former [-0.53730869]
Later 0.42925669866235444
RS [-0.10805199]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 2.7878723
B 1.9206525
E 41.5518642140288
Former [-0.26155095]
Later 1.5510546210161658
RS [1.28950367]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y 0.8845855
B 1.9206525
E 33.77172594394637
Former [0.04224098]
Later 1.3920761665743868
RS [1.43431715]
--------------------------------
U 0.008559834
A -0.5080535475323766
Y -0.0785259
B 1.9206525
E 36.6779

In [94]:
for i in range(len(NDCG_List)):
    print(NDCG_List[i],MAP_List[i])

# NDCG For Different Dimensions

In [111]:
######## code here !!!!

(10, 20)

In [69]:
def topN(sortlist,n):
    topList = []
    for i in range(n):
        topList.append(sortlist.index(max(sortlist)))
        #print(max(sortlist))
        #print(sortlist.index(max(sortlist)))
        sortlist[sortlist.index(max(sortlist))] = -1000000000
    return topList

In [70]:
count_0_all = []
for i in range(len(testRS)):
    top_0 = topN(list(testRS[i]),int(np.sum(target[i])))
    count_0_all.append(top_0)
    print(top_0)

acc_0 = 0
total = 0
for i in range(len(count_0_all)):
    for j in range(len(count_0_all[i])):
        #print(int(np.sum(target[i])))
        total+=int(np.sum(target[i]))
        if count_0_all[i][j] < int(np.sum(target[i])): #代表是0或1 (也就是target)
            acc_0 += 1
avg_acc = acc_0/100
print('avg_accuarcy for count_0:',avg_acc)
print(acc_0)

[0, 2, 1]
[3, 6, 2]
[1, 2, 13, 4, 5, 3, 17]
[1, 10, 8, 2, 5, 4]
[4, 1, 12]
[1, 15, 11]
[2, 1, 10, 0]
[3, 2, 5, 7, 4, 18]
[3, 18, 8, 5, 13]
[12, 16, 7, 0, 9]
avg_accuarcy for count_0: 0.24
24


# TOP1,TOP3,TOP5

In [71]:
def F1_score(prec,rec):
    f1 = (2*prec*rec)/(prec+rec)
    return f1

# NDCG 

In [172]:
a_list = [0.02162337, 0.02162659, 0.00240219, 0.00780985, 0.02162318, 0.00780592, 0.00780849]
softmax(a_list)

array([0.14409628, 0.14409674, 0.14135303, 0.14211949, 0.14409625,
       0.14211893, 0.14211929])